In [6]:
# ==============================================================================
#  الكود النهائي الكامل والمُصحح (أمر واحد للتشغيل) - إصدار 13.0 (النهائي)
#  (استراتيجية الزحف العميق للأقسام - النسخة الأنظف والأسرع)
# ==============================================================================

# --- أولاً: تثبيت الأدوات اللازمة ---
!pip install --upgrade selenium pandas tqdm requests undetected-chromedriver fake-useragent
!apt-get update
!apt-get install -y wget curl unzip

# --- ثانياً: تثبيت Google Chrome ومتصفح التشغيل الخاص به ---
print("🔧 جاري تثبيت Google Chrome...")
!wget -q -O - https://dl-ssl.google.com/linux/linux_signing_key.pub | apt-key add -
!echo "deb [arch=amd64] http://dl.google.com/linux/chrome/deb/ stable main" >> /etc/apt/sources.list.d/google-chrome.list
!apt-get update
!apt-get install -y google-chrome-stable

# التحقق من التثبيت
!which google-chrome
!google-chrome --version
print("✅ تم تثبيت Chrome بنجاح")

# تنظيف أي إصدارات قديمة
!pkill -f chromedriver || true
!pkill -f chrome || true
!rm -f /usr/bin/chromedriver || true
!rm -rf chromedriver-linux64* || true

# تنزيل ChromeDriver المتوافق (إصدار 142)
print("🔧 جاري تثبيت ChromeDriver 142...")
!wget -N https://storage.googleapis.com/chrome-for-testing-public/142.0.7444.59/linux64/chromedriver-linux64.zip
!unzip -o chromedriver-linux64.zip
!cp chromedriver-linux64/chromedriver /usr/bin/chromedriver
!chmod +x /usr/bin/chromedriver

print("✅ تم تثبيت ChromeDriver المتوافق بنجاح")

# ----------------------------------------------------------------------
# --- ثالثاً: استيراد مكتبات بايثون ---
import os
import re
import time
import random
import pandas as pd
from tqdm import tqdm
from concurrent.futures import ThreadPoolExecutor, as_completed
import threading
import requests
import xml.etree.ElementTree as ET

from selenium import webdriver
from selenium.webdriver.chrome.service import Service
from selenium.webdriver.common.by import By
from selenium.webdriver.chrome.options import Options
from selenium.webdriver.support.ui import WebDriverWait
from selenium.webdriver.support import expected_conditions as EC
from selenium.common.exceptions import WebDriverException, TimeoutException, NoSuchElementException

# استيراد السلاح السري
import undetected_chromedriver as uc

# --- رابعاً: تعريف الكلاسات والدوال ---

# --- نظام التخزين الذكي ---
class SmartStorage:
    def __init__(self):
        self.drive_mounted = False
        self.local_folder = "/content/Scraped_Data"
        self.drive_folder = "/content/drive/MyDrive/Scraped_Data"
        self.setup_storage()

    def setup_storage(self):
        try:
            from google.colab import drive
            print("🔄 محاولة توصيل Google Drive...")
            drive.mount('/content/drive')
            self.drive_mounted = True
            os.makedirs(self.drive_folder, exist_ok=True)
            print(f"✅ تم توصيل Google Drive بنجاح: {self.drive_folder}")
        except Exception as e:
            self.drive_mounted = False
            os.makedirs(self.local_folder, exist_ok=True)
            print(f"⚠️ فشل توصيل Drive. استخدام التخزين المحلي: {self.local_folder}")

    def get_output_path(self, filename):
        if self.drive_mounted:
            return f"{self.drive_folder}/{filename}"
        else:
            return f"{self.local_folder}/{filename}"

# --- إعداد المتصفح (استخدام Undetected + Headless) ---
def setup_driver_advanced():
    """إعداد متصفح متقدم (باستخدام Undetected-Chromedriver)"""
    chrome_options = uc.ChromeOptions()
    chrome_options.binary_location = "/usr/bin/google-chrome-stable"

    chrome_options.add_argument('--headless')
    chrome_options.add_argument('--no-sandbox')
    chrome_options.add_argument('--disable-dev-shm-usage')
    chrome_options.add_argument('--disable-gpu')
    chrome_options.add_argument('--disable-extensions')
    chrome_options.add_argument('--disable-plugins')

    user_agents = [
        "Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/142.0.0.0 Safari/537.36",
        "Mozilla/5.0 (Macintosh; Intel Mac OS X 10_15_7) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/142.0.0.0 Safari/537.36"
    ]
    user_agent = random.choice(user_agents)
    chrome_options.add_argument(f'--user-agent={user_agent}')

    try:
        driver = uc.Chrome(options=chrome_options, driver_executable_path="/usr/bin/chromedriver")
        driver.set_page_load_timeout(REQUEST_TIMEOUT)
        driver.set_script_timeout(REQUEST_TIMEOUT)
        return driver
    except Exception as e:
        print(f"❌ فشل إعداد المتصفح (Undetected): {e}")
        return None

# --- [تم التعديل] دالة جمع الروابط (نسخة 13.0: النهائية والأسرع) ---
def get_all_article_urls_advanced():
    """جمع روابط المقالات عبر زيارة الصفحات الأولى للأقسام (الأسرع)"""
    print("🚀 بدء جمع الروابط (إصدار 13.0 - النهائي)...")

    CATEGORIES_TO_SCRAPE = [
        "https://www.okaz.com.sa/local",
        "https://www.okaz.com.sa/politics",
        "https://www.okaz.com.sa/economy",
        "https://www.okaz.com.sa/sports",
        "https://www.okaz.com.sa/culture",
        "https://www.okaz.com.sa/variety"
    ]

    driver = None
    article_urls = set()
    article_pattern = re.compile(r'okaz\.com\.sa/.+/\d{7,}')

    try:
        driver = setup_driver_advanced()
        if not driver:
            print("❌ فشل إعداد المتصفح لجمع الروابط")
            return []

        for category_url in CATEGORIES_TO_SCRAPE:
            try:
                print(f"🔍 جاري زيارة قسم: {category_url}")
                driver.get(category_url)
                time.sleep(3) # انتظار تحميل الصفحة

                # [تم التعديل] مسح الصفحة مرة واحدة فقط (لأن "المزيد" لا يعمل)
                all_links = driver.find_elements(By.TAG_NAME, "a")
                found_in_section = 0
                for link in all_links:
                    try:
                        href = link.get_attribute("href")
                        if href and article_pattern.search(href):
                            if href not in article_urls:
                                article_urls.add(href)
                                found_in_section += 1
                    except Exception:
                        continue
                print(f"    ✅ تم إضافة {found_in_section} رابط جديد من هذا القسم.")

            except Exception as e:
                print(f"⚠️ فشل معالجة القسم {category_url}: {e}")
                continue

        driver.quit()
        print("ℹ️ تم إغلاق متصفح جمع الروابط.")

        if not article_urls:
            print("❌ لم يتم العثور على أي روابط مقالات في جميع الأقسام!")
            return []

        final_urls = list(article_urls)
        print(f"🎯 إجمالي الروابط الفريدة التي تم جمعها من جميع الأقسام: {len(final_urls)}")

        return final_urls

    except Exception as e:
        print(f"❌ فشل جمع الروابط بشكل كامل: {e}")
        if driver:
            driver.quit()
        return []


# --- دالة سحب المقال (تبقى كما هي) ---
def scrape_article_advanced(url):
    """سحب مقال مع معالجة متقدمة للبيانات"""
    time.sleep(random.uniform(1, DELAY_BETWEEN_REQUESTS))
    driver = None
    try:
        driver = setup_driver_advanced()
        if not driver: return None
        driver.get(url)
        WebDriverWait(driver, 15).until(EC.presence_of_element_located((By.TAG_NAME, "body")))

        data = {'title': 'غير معروف', 'content': 'غير متوفر', 'url': url, 'words_count': 0, 'success': True}

        # استخراج العنوان
        title_selectors = ['h1', 'h1.article-title', 'h1.title', '.headline h1', 'title']
        for selector in title_selectors:
            try:
                if selector == 'title':
                    data['title'] = driver.title
                    if data['title'] and data['title'] != 'غير معروف': break
                else:
                    title_elem = driver.find_element(By.CSS_SELECTOR, selector)
                    if title_elem.text.strip():
                        data['title'] = title_elem.text.strip()
                        break
            except: continue

        # استخراج المحتوى
        content_selectors = ['article', '.article-content', '.post-content', '.content', '.article-body']
        content_text = ""
        for selector in content_selectors:
            try:
                content_elems = driver.find_elements(By.CSS_SELECTOR, selector)
                for elem in content_elems:
                    text = elem.text.strip()
                    if len(text) > len(content_text): content_text = text
            except: continue

        data['content'] = re.sub(r'\s+', ' ', content_text)
        data['words_count'] = len(data['content'].split())

        if data['words_count'] < 30:
            data['success'] = False
        else:
            print(f"✅ تم سحب: {data['title'][:60]}... ({data['words_count']} كلمة)")

        driver.quit()
        return data if data['success'] else None
    except Exception as e:
        if driver: driver.quit()
        return None

# --- دالة الحفظ الآمن (تبقى كما هي) ---
CSV_LOCK = threading.Lock()
def save_articles_safe(articles, filename):
    if not articles: return
    try:
        df = pd.DataFrame(articles)
        with CSV_LOCK:
            if os.path.exists(filename):
                existing_df = pd.read_csv(filename)
                combined_df = pd.concat([existing_df, df], ignore_index=True)
                combined_df = combined_df.drop_duplicates(subset=['url'], keep='last')
                combined_df.to_csv(filename, index=False, encoding='utf-8-sig')
            else:
                df.to_csv(filename, index=False, encoding='utf-8-sig')
    except Exception as e:
        print(f"❌ خطأ في الحفظ: {e}")

# --- الدالة الرئيسية (المدير) ---
def main_full():
    print("🚀 بدء السحب الموسع...")
    start_time = time.time()
    print("🔍 جاري جمع روابط المقالات...")

    all_urls = get_all_article_urls_advanced()

    if not all_urls:
        print("❌ لم يتم العثور على أي مقالات")
        return

    existing_urls = set()
    if os.path.exists(OUTPUT_FILE):
        try:
            existing_df = pd.read_csv(OUTPUT_FILE)
            existing_urls = set(existing_df['url'].tolist())
            print(f"📖 يوجد {len(existing_urls)} مقال مسبقاً في الملف")
        except Exception as e:
            print(f"⚠️ لم نتمكن من قراءة الملف القديم: {e}")

    new_urls = [url for url in all_urls if url not in existing_urls]

    if not new_urls:
        print("🎉 لا توجد مقالات جديدة لسحبها. الملف محدث!")
        return

    # تحديد العدد المطلوب بناءً على الإعدادات
    # [تعديل] سنقوم بسحب كل المقالات الجديدة التي نجدها، حتى حد الـ 200
    urls_to_scrape = new_urls[:MAX_ARTICLES_TO_SCRAPE]
    print(f"ℹ️ يوجد {len(new_urls)} مقال جديد متاح. سنقوم بسحب {len(urls_to_scrape)} مقال (حسب الإعدادات).")

    print(f"🔄 جاري سحب {len(urls_to_scrape)} مقال جديد باستخدام {MAX_THREADS} خيوط...")

    results = []
    failed_urls = []
    temp_results_buffer = []

    with ThreadPoolExecutor(max_workers=MAX_THREADS) as executor:
        future_to_url = {executor.submit(scrape_article_advanced, url): url for url in urls_to_scrape}

        for future in tqdm(as_completed(future_to_url), total=len(urls_to_scrape), desc="سحب المقالات"):
            url = future_to_url[future]
            try:
                result = future.result()
                if result:
                    results.append(result)
                    temp_results_buffer.append(result)
                    if len(temp_results_buffer) >= 10: # نحفظ كل 10 مقالات
                        save_articles_safe(temp_results_buffer, OUTPUT_FILE)
                        print(f"💾 ... تم حفظ دفعة من {len(temp_results_buffer)} مقال ...")
                        temp_results_buffer = []
                else:
                    failed_urls.append(url)
            except Exception as e:
                failed_urls.append(url)

    if temp_results_buffer: # حفظ البقية
        save_articles_safe(temp_results_buffer, OUTPUT_FILE)
        print(f"💾 ... تم حفظ الدفعة الأخيرة ...")

    end_time = time.time()
    total_time = end_time - start_time
    print(f"\n" + "="*50)
    print(f"🎉 اكتمل السحب!")
    print(f"⏰ الوقت: {total_time/60:.1f} دقيقة")
    print(f"📊 النتائج: ✅ {len(results)} ناجح | ❌ {len(failed_urls)} فاشل")
    print(f"💾 الملف: {OUTPUT_FILE}")
    print("="*50)


# --- خامساً: الإعدادات والتشغيل ---

# تهيئة نظام التخزين
print("🚀 بدء إعداد نظام التخزين...")
storage = SmartStorage()
OUTPUT_FILE = storage.get_output_path("okaz_articles_full.csv")

# ==================================================================
# ## الإعدادات المتقدمة (النهائية) ##
# ==================================================================
MAX_THREADS = 5            # السرعة: 5 متصفحات متوازية
MAX_ARTICLES_TO_SCRAPE = 200 # الكمية: 200 مقال كحد أقصى (لكل تشغيلة)
REQUEST_TIMEOUT = 30
DELAY_BETWEEN_REQUESTS = 2

print(f"📊 إعدادات السحب:")
print(f"    🧵 الخيوط: {MAX_THREADS}")
print(f"    📄 المقالات: {MAX_ARTICLES_TO_SCRAPE}")
print(f"    💾 الحفظ في: {OUTPUT_FILE}")
# ==================================================================


# --- نقطة البداية ---
if __name__ == "__main__":
    print("=" * 50)
    print("🚀 برنامج سحب مقالات Okaz - (إصدار 13 - النهائي)")
    print("=" * 50)
    main_full()

Hit:1 https://dl.google.com/linux/chrome/deb stable InRelease
Hit:2 https://cloud.r-project.org/bin/linux/ubuntu jammy-cran40/ InRelease
Hit:3 https://cli.github.com/packages stable InRelease
Hit:4 https://developer.download.nvidia.com/compute/cuda/repos/ubuntu2204/x86_64  InRelease
Hit:5 http://security.ubuntu.com/ubuntu jammy-security InRelease
Hit:6 http://archive.ubuntu.com/ubuntu jammy InRelease
Hit:7 https://ppa.launchpadcontent.net/deadsnakes/ppa/ubuntu jammy InRelease
Hit:8 https://ppa.launchpadcontent.net/graphics-drivers/ppa/ubuntu jammy InRelease
Hit:9 http://archive.ubuntu.com/ubuntu jammy-updates InRelease
Hit:10 https://r2u.stat.illinois.edu/ubuntu jammy InRelease
Hit:11 https://ppa.launchpadcontent.net/ubuntugis/ppa/ubuntu jammy InRelease
Hit:12 http://archive.ubuntu.com/ubuntu jammy-backports InRelease
Reading package lists... Done
W: Target Packages (main/binary-amd64/Packages) is configured multiple times in /etc/apt/sources.list.d/google-chrome.list:3 and /etc/apt/so

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).
✅ تم توصيل Google Drive بنجاح: /content/drive/MyDrive/Scraped_Data
📊 إعدادات السحب:
    🧵 الخيوط: 5
    📄 المقالات: 200
    💾 الحفظ في: /content/drive/MyDrive/Scraped_Data/okaz_articles_full.csv
🚀 برنامج سحب مقالات Okaz - (إصدار 13 - النهائي)
🚀 بدء السحب الموسع...
🔍 جاري جمع روابط المقالات...
🚀 بدء جمع الروابط (إصدار 13.0 - النهائي)...
🔍 جاري زيارة قسم: https://www.okaz.com.sa/local
    ✅ تم إضافة 30 رابط جديد من هذا القسم.
🔍 جاري زيارة قسم: https://www.okaz.com.sa/politics
    ✅ تم إضافة 17 رابط جديد من هذا القسم.
🔍 جاري زيارة قسم: https://www.okaz.com.sa/economy
    ✅ تم إضافة 17 رابط جديد من هذا القسم.
🔍 جاري زيارة قسم: https://www.okaz.com.sa/sports
    ✅ تم إضافة 16 رابط جديد من هذا القسم.
🔍 جاري زيارة قسم: https://www.okaz.com.sa/culture
    ✅ تم إضافة 17 رابط جديد من هذا القسم.
🔍 جاري زيارة قسم: https://www.okaz.com.sa/variety
    ✅ تم إضافة 15 رابط جد

In [7]:
import pandas as pd
import re
import os

# --- الإعدادات ---
# تأكد من أن هذه المسارات مطابقة للمسارات في كود السحب

DRIVE_FOLDER = "/content/drive/MyDrive/Scraped_Data"
INPUT_FILE = os.path.join(DRIVE_FOLDER, "okaz_articles_full.csv")
OUTPUT_FILE_CLEANED = os.path.join(DRIVE_FOLDER, "okaz_articles_cleaned.csv")

# --- 1. تحميل البيانات ---
print(f"🔄 جاري تحميل الملف: {INPUT_FILE}")
try:
    df = pd.read_csv(INPUT_FILE)
    print(f"✅ تم تحميل {len(df)} مقالاً.")
except FileNotFoundError:
    print(f"❌ خطأ: لم يتم العثور على الملف. تأكد من تشغيل كود السحب أولاً.")
    # يمكنك إيقاف التنفيذ هنا إذا لم يتم العثور على الملف
    # raise
except Exception as e:
    print(f"❌ خطأ غير متوقع أثناء قراءة الملف: {e}")
    # raise

# --- 2. دالة التنظيف ---
def clean_article_text(text):
    if not isinstance(text, str):
        return "" # إرجاع نص فارغ إذا كانت البيانات ليست نصية (مثل NaN)

    # إزالة الروابط
    text = re.sub(r'http\S+|www\S+|https\S+', '', text, flags=re.MULTILINE)

    # إزالة الكلمات المفتاحية الشائعة (يمكن إضافة المزيد)
    # (re.IGNORECASE يتجاهل حالة الأحرف - re.DOTALL يجعل . تشمل الأسطر الجديدة)
    patterns_to_remove = [
        r'اقرأ أيضاً:.*',
        r'اقرأ أيضا:.*',
        r'تابعنا على.*',
        r'لمزيد من التفاصيل.*',
        r'للمزيد.*',
        r'شارك.*'
    ]

    for pattern in patterns_to_remove:
        text = re.sub(pattern, '', text, flags=re.IGNORECASE | re.DOTALL)

    # إزالة الأسطر الفارغة الزائدة (سطرين فارغين أو أكثر -> سطر واحد)
    text = re.sub(r'\n\s*\n', '\n', text)

    # إزالة المسافات البيضاء الزائدة
    text = ' '.join(text.split())

    return text.strip() # .strip() لإزالة أي مسافات في البداية أو النهاية

# --- 3. تطبيق التنظيف ---
print("🧹 بدء عملية تنظيف عمود 'content'...")

# إنشاء عمود جديد "cleaned_content" للحفاظ على الأصل
df['cleaned_content'] = df['content'].apply(clean_article_text)

# حساب عدد الكلمات الجديد
df['cleaned_words_count'] = df['cleaned_content'].apply(lambda x: len(x.split()))

print("✅ اكتمل التنظيف.")

# --- 4. عرض مثال (قبل وبعد) ---
print("\n" + "="*50)
print("🕵️‍♂️ مثال على التنظيف (المقال رقم 5):")
print("--- قبل ---")
print(df['content'].iloc[5][:500] + "...") # عرض أول 500 حرف
print("\n--- بعد ---")
print(df['cleaned_content'].iloc[5][:500] + "...")
print("\n" + "="*50)

# --- 5. حفظ الملف النظيف ---
print(f"💾 جاري حفظ الملف النظيف في: {OUTPUT_FILE_CLEANED}")
df.to_csv(OUTPUT_FILE_CLEANED, index=False, encoding='utf-8-sig')
print("🎉 تم الحفظ بنجاح!")

# عرض إحصائيات سريعة
print("\n📊 إحصائيات (بعد التنظيف):")
print(f"  متوسط عدد الكلمات (الأصلي): {df['words_count'].mean():.0f}")
print(f"  متوسط عدد الكلمات (النظيف): {df['cleaned_words_count'].mean():.0f}")

🔄 جاري تحميل الملف: /content/drive/MyDrive/Scraped_Data/okaz_articles_full.csv
✅ تم تحميل 143 مقالاً.
🧹 بدء عملية تنظيف عمود 'content'...
✅ اكتمل التنظيف.

🕵️‍♂️ مثال على التنظيف (المقال رقم 5):
--- قبل ---
عكاظ > ازياء السعودية تكرّس مكانتها مركزاً عالمياً لصناعة الجمال 2 نوفمبر 2025 - 16:18 | آخر تحديث 2 نوفمبر 2025 - 16:18 استمع إلى المقال --:-- ذكرى السلمي (جدة) zekraalsolami@ شهد قطاع الجمال هذا الأسبوع تأكيداً جديداً على مكانة السوق السعودية كمحرك أساسي للنمو في المنطقة، بعدما أعلن أحد المعارض مشاركة واسعة لعلامات دولية جاءت من 37 دولة مختلفة، من بينها فرنسا وإيطاليا والبرازيل وكوريا والإمارات. وجاءت هذه المشاركة الكثيفة لتعكس اهتماماً متزايداً من الشركات العالمية بدخول السوق السعودية والاستف...

--- بعد ---
عكاظ > ازياء السعودية تكرّس مكانتها مركزاً عالمياً لصناعة الجمال 2 نوفمبر 2025 - 16:18 | آخر تحديث 2 نوفمبر 2025 - 16:18 استمع إلى المقال --:-- ذكرى السلمي (جدة) zekraalsolami@ شهد قطاع الجمال هذا الأسبوع تأكيداً جديداً على مكانة السوق السعودية كمحرك أساسي للنمو في المنطقة، ب

In [8]:
# --- 1. تثبيت المكتبات اللازمة ---
print("🔧 جاري تثبيت مكتبة NLTK (لتحليل النصوص)...")
!pip install nltk
print("✅ اكتمل التثبيت.")

# --- 2. استيراد المكتبات ---
import pandas as pd
import re
import os
import nltk
import string
from collections import Counter

# --- 3. تحميل البيانات النظيفة ---
DRIVE_FOLDER = "/content/drive/MyDrive/Scraped_Data"
CLEANED_FILE = os.path.join(DRIVE_FOLDER, "okaz_articles_cleaned.csv")
FREQUENCY_FILE = os.path.join(DRIVE_FOLDER, "okaz_word_frequency.csv")

print(f"🔄 جاري تحميل الملف النظيف: {CLEANED_FILE}")
try:
    df = pd.read_csv(CLEANED_FILE)
    print(f"✅ تم تحميل {len(df)} مقالاً نظيفاً.")
except FileNotFoundError:
    print(f"❌ خطأ: لم يتم العثور على الملف النظيف. يرجى التأكد من تشغيل كود التنظيف (الخطوة السابقة) بنجاح.")
    # raise
except Exception as e:
    print(f"❌ خطأ غير متوقع أثناء قراءة الملف: {e}")
    # raise

# --- 4. إعداد الكلمات المستبعدة (Stop Words) ---
print("📚 جاري تحميل قائمة الكلمات المستبعدة العربية...")
try:
    nltk.download('stopwords')
    arabic_stopwords = set(nltk.corpus.stopwords.words('arabic'))
except Exception as e:
    print(f"⚠️ فشل تحميل قائمة NLTK. سنستخدم قائمة أساسية. الخطأ: {e}")
    arabic_stopwords = set(["من", "في", "على", "إلى", "و", "أن", "أو", "هو", "هي", "لا", "ما", "عن", "مع", "قد", "تم", "كان", "هذا", "هذه", "ذلك", "التي", "الذي", "فيها", "فيها", "كما", "إلا", "أنه", "له", "به", "حيث", "بأن"])

# إضافة كلمات مستبعدة خاصة بنا (ضجيج من الموقع)
custom_stopwords = set([
    'عكاظ', 'السعودية', 'أخبار', 'المملكة', 'العربية', 'السعودي', 'السعودية',
    'جدة', 'الرياض', 'نوفمبر', 'أكتوبر', 'تحديث', 'آخر', 'استمع', 'للمقال',
    'كلمة', 'وقال', 'وأضاف', 'إلى', 'أن', 'في', 'من', 'على', 'و', 'أو',
    'التي', 'الذي', 'إلا', 'عن', 'مع', 'هذا', 'هذه', 'ذلك', 'كان', 'تم',
    'اليوم', 'أمس', 'العالم', 'الدولية', 'الدولي', 'العالمي', 'موقع', 'عبر',
    'خلال', 'بعد', 'قبل', 'يكون', 'تكون', 'لـ', 'بـ', 'الـ', 'هو', 'هي', 'له', 'لها',
    'ألف', 'مليون', 'مليار', 'ريال', 'دولار', 'العام', 'الماضي', 'الجديد', 'الأول', 'الثاني'
])

# دمج القائمتين
stop_words = arabic_stopwords.union(custom_stopwords)
print(f"✅ جاهز. إجمالي الكلمات المستبعدة: {len(stop_words)}")

# --- 5. دالة لتنظيف وتطبيع النص للتحليل ---
def normalize_arabic(text):
    if not isinstance(text, str):
        return ""

    # إزالة التشكيل
    text = re.sub(r'[\u064B-\u0652]', '', text)
    # إزالة التطويل
    text = re.sub(r'ـ', '', text)
    # إزالة الأرقام
    text = re.sub(r'\d+', '', text)
    # إزالة علامات الترقيم الإنجليزية والعربية
    punctuation = string.punctuation + '،؛؟«»'
    text = text.translate(str.maketrans('', '', punctuation))

    # توحيد الحروف
    text = re.sub(r'[أإآ]', 'ا', text)
    text = re.sub(r'ى', 'ي', text)
    text = re.sub(r'ة', 'ه', text)

    return text

# --- 6. المعالجة والعد ---
print("🔄 جاري معالجة جميع المقالات...")

# دمج كل النصوص في نص واحد عملاق
# (التأكد من أننا نستخدم العمود النظيف الذي أنشأناه)
if 'cleaned_content' in df.columns:
    all_text = ' '.join(df['cleaned_content'].dropna())
else:
    print("⚠️ لم يتم العثور على عمود 'cleaned_content'. سنستخدم 'content' كبديل.")
    all_text = ' '.join(df['content'].dropna())

# تنظيف وتطبيع النص العملاق
normalized_text = normalize_arabic(all_text)

# تقسيم النص إلى كلمات (tokens)
words = normalized_text.split()

# فلترة الكلمات
print("⏳ جاري فلترة الكلمات (إزالة المستبعدة والقصيرة)...")
filtered_words = [word for word in words if word not in stop_words and len(word) > 2]

# عد الكلمات الأكثر تكراراً
print("📊 جاري عد الكلمات الأكثر تكراراً...")
word_counts = Counter(filtered_words)

# --- 7. حفظ وعرض النتائج ---
print("✅ اكتمل العد! إليك أعلى 10 كلمات:")

# تحويل النتائج إلى DataFrame
freq_df = pd.DataFrame(word_counts.most_common(50), columns=['الكلمة', 'التكرار'])

# طباعة أعلى 10
print(freq_df.head(10).to_string(index=False))

# حفظ الملف
try:
    freq_df.to_csv(FREQUENCY_FILE, index=False, encoding='utf-8-sig')
    print(f"\n🎉 تم حفظ أكثر 50 كلمة تكراراً في ملف:")
    print(f"{FREQUENCY_FILE}")
except Exception as e:
    print(f"\n❌ فشل حفظ ملف التكرار: {e}")

print("\nانتهت المهمة. أصبح لديك ملف CSV يحتوي على الكلمات المفتاحية لمقالات عكاظ.")


🔧 جاري تثبيت مكتبة NLTK (لتحليل النصوص)...
✅ اكتمل التثبيت.
🔄 جاري تحميل الملف النظيف: /content/drive/MyDrive/Scraped_Data/okaz_articles_cleaned.csv
✅ تم تحميل 143 مقالاً نظيفاً.
📚 جاري تحميل قائمة الكلمات المستبعدة العربية...
✅ جاهز. إجمالي الكلمات المستبعدة: 737
🔄 جاري معالجة جميع المقالات...
⏳ جاري فلترة الكلمات (إزالة المستبعدة والقصيرة)...
📊 جاري عد الكلمات الأكثر تكراراً...
✅ اكتمل العد! إليك أعلى 10 كلمات:
  الكلمة  التكرار
     الي      462
     علي      421
     اخر      156
  المقال      103
السعوديه       77
     جده       66
   العمل       64
     انه       57
 المملكه       52
    محمد       49

🎉 تم حفظ أكثر 50 كلمة تكراراً في ملف:
/content/drive/MyDrive/Scraped_Data/okaz_word_frequency.csv

انتهت المهمة. أصبح لديك ملف CSV يحتوي على الكلمات المفتاحية لمقالات عكاظ.


[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Unzipping corpora/stopwords.zip.


In [9]:
# --- 1. تثبيت المكتبات اللازمة ---
print("🔧 جاري تثبيت مكتبة Scikit-learn (لتعلم الآلة)...")
!pip install scikit-learn nltk
print("✅ اكتمل التثبيت.")

# --- 2. استيراد المكتبات ---
import pandas as pd
import re
import os
import nltk
import string
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.decomposition import LatentDirichletAllocation

# --- 3. تحميل البيانات النظيفة ---
DRIVE_FOLDER = "/content/drive/MyDrive/Scraped_Data"
CLEANED_FILE = os.path.join(DRIVE_FOLDER, "okaz_articles_cleaned.csv")

print(f"🔄 جاري تحميل الملف النظيف: {CLEANED_FILE}")
try:
    df = pd.read_csv(CLEANED_FILE)
    # التأكد من أن العمود نظيف وجاهز
    df['cleaned_content'] = df['cleaned_content'].fillna('')
    print(f"✅ تم تحميل {len(df)} مقالاً نظيفاً.")
except FileNotFoundError:
    print(f"❌ خطأ: لم يتم العثور على الملف النظيف. يرجى التأكد من تشغيل كود التنظيف (الخطوة السابقة) بنجاح.")
    raise

# --- 4. إعداد الكلمات المستبعدة (Stop Words) ---
# (نفس الكود من المرحلة السابقة لإعادة الاستخدام)
print("📚 جاري تحميل قائمة الكلمات المستبعدة العربية...")
try:
    nltk.download('stopwords')
    arabic_stopwords = set(nltk.corpus.stopwords.words('arabic'))
except Exception as e:
    arabic_stopwords = set(["من", "في", "على", "إلى", "و", "أن", "أو", "هو", "هي", "لا", "ما", "عن", "مع", "قد", "تم", "كان", "هذا", "هذه", "ذلك", "التي", "الذي", "فيها", "فيها", "كما", "إلا", "أنه", "له", "به", "حيث", "بأن"])

custom_stopwords = set([
    'عكاظ', 'السعودية', 'أخبار', 'المملكة', 'العربية', 'السعودي', 'السعودية',
    'جدة', 'الرياض', 'نوفمبر', 'أكتوبر', 'تحديث', 'آخر', 'استمع', 'للمقال',
    'كلمة', 'وقال', 'وأضاف', 'إلى', 'أن', 'في', 'من', 'على', 'و', 'أو',
    'التي', 'الذي', 'إلا', 'عن', 'مع', 'هذا', 'هذه', 'ذلك', 'كان', 'تم',
    'اليوم', 'أمس', 'العالم', 'الدولية', 'الدولي', 'العالمي', 'موقع', 'عبر',
    'خلال', 'بعد', 'قبل', 'يكون', 'تكون', 'لـ', 'بـ', 'الـ', 'هو', 'هي', 'له', 'لها',
    'ألف', 'مليون', 'مليار', 'ريال', 'دولار', 'العام', 'الماضي', 'الجديد', 'الأول', 'الثاني',
    'الي', 'علي', 'انه', 'اخر' # إضافة الكلمات الشائعة من تحليلنا السابق
])
stop_words = list(arabic_stopwords.union(custom_stopwords))
print(f"✅ جاهز. إجمالي الكلمات المستبعدة: {len(stop_words)}")

# --- 5. تحويل النص إلى أرقام (Vectorization) ---
print("🔄 جاري تحويل النصوص إلى مصفوفة أرقام (TF-IDF)...")

# سنستخدم TfidfVectorizer لأنه يعطي وزناً للكلمات المهمة
# max_df=0.9: تجاهل الكلمات التي تظهر في أكثر من 90% من المقالات (كلمات شائعة جداً)
# min_df=3: تجاهل الكلمات التي ظهرت في أقل من 3 مقالات (كلمات نادرة جداً)
vectorizer = TfidfVectorizer(
    stop_words=stop_words,
    preprocessor=normalize_arabic, # استخدام دالتنا للتنظيف
    max_df=0.9,
    min_df=3,
    use_idf=True
)

# [خطأ شائع] نحتاج لدالة التطبيع هنا
def normalize_arabic(text):
    if not isinstance(text, str): return ""
    text = re.sub(r'[\u064B-\u0652]', '', text)
    text = re.sub(r'ـ', '', text)
    text = re.sub(r'\d+', '', text)
    punctuation = string.punctuation + '،؛؟«»'
    text = text.translate(str.maketrans('', '', punctuation))
    text = re.sub(r'[أإآ]', 'ا', text)
    text = re.sub(r'ى', 'ي', text)
    text = re.sub(r'ة', 'ه', text)
    return text

# تطبيق التحويل
tfidf_matrix = vectorizer.fit_transform(df['cleaned_content'])
print("✅ اكتمل التحويل.")

# --- 6. بناء نموذج المواضيع (LDA) ---
# سنطلب منه البحث عن 5 مواضيع
num_topics = 5

print(f"🧠 بدء بناء نموذج تعلم الآلة (LDA) للبحث عن {num_topics} مواضيع...")
# نستخدم LDA. n_components هو عدد المواضيع
lda = LatentDirichletAllocation(
    n_components=num_topics,
    random_state=42, # للتثبيت على نفس النتائج
    n_jobs=-1 # استخدام كل المعالجات للسرعة
)
lda.fit(tfidf_matrix)
print("✅ اكتمل بناء النموذج!")

# --- 7. عرض النتائج (الكلمات المفتاحية لكل موضوع) ---
print("\n" + "="*60)
print(f"🎉 النتائج: أهم 10 كلمات مفتاحية لكل موضوع من المواضيع الـ {num_topics}")
print("="*60)

# الحصول على أسماء الكلمات (Features)
feature_names = vectorizer.get_feature_names_out()

for topic_idx, topic in enumerate(lda.components_):
    # ترتيب الكلمات في هذا الموضوع من الأهم إلى الأقل أهمية
    top_words_indices = topic.argsort()[:-10 - 1:-1]
    # جلب أسماء الكلمات
    top_words = [feature_names[i] for i in top_words_indices]

    print(f"\n🎨 **الموضوع رقم #{topic_idx + 1}:**")
    print(" | ".join(top_words))

print("\n" + "="*60)
print("انتهت المهمة. هذه هي المجموعات الرئيسية للمواضيع في مقالات عكاظ التي جمعتها.")

🔧 جاري تثبيت مكتبة Scikit-learn (لتعلم الآلة)...
✅ اكتمل التثبيت.
🔄 جاري تحميل الملف النظيف: /content/drive/MyDrive/Scraped_Data/okaz_articles_cleaned.csv
✅ تم تحميل 143 مقالاً نظيفاً.
📚 جاري تحميل قائمة الكلمات المستبعدة العربية...
✅ جاهز. إجمالي الكلمات المستبعدة: 741
🔄 جاري تحويل النصوص إلى مصفوفة أرقام (TF-IDF)...


[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
/usr/local/lib/python3.12/dist-packages/sklearn/feature_extraction/text.py:402: UserWarning: Your stop_words may be inconsistent with your preprocessing. Tokenizing the stop words generated tokens ['اب', 'ابتدا', 'ابدا', 'ابريل', 'ابو', 'اجل', 'اجمع', 'احد', 'احدي', 'اخ', 'اخبار', 'اخبر', 'اخذ', 'اخو', 'اذ', 'اذا', 'اذار', 'اذما', 'اذن', 'اربع', 'اربعاء', 'اربعمئه', 'اربعمائه', 'اربعه', 'ارتد', 'اري', 'ازاء', 'اسكن', 'اصبح', 'اصلا', 'اض', 'اضحي', 'اطعم', 'اعطي', 'اعلم', 'اغسطس', 'اف', 'افريل', 'افعل', 'افعله', 'اقبل', 'اقل', 'اكتوبر', 'اكثر', 'ال', 'الا', 'الالاء', 'الالي', 'الان', 'الاول', 'الدوليه', 'السعوديه', 'العربيه', 'الف', 'الفي', 'المملكه', 'اليك', 'اليكم', 'اليكما', 'اليكن', 'ام', 'اما', 'امام', 'امامك', 'امد', 'امس', 'امسي', 'امين', 'ان', 'انا', 'اناء', 'انبا', 'انبري', 'انت', 'انتم', 'انتما', 'انتن', 'انشا', 'انفا', 'انفك', 'انما', 'اني', 'اه', 'اها', 'اهلا

✅ اكتمل التحويل.
🧠 بدء بناء نموذج تعلم الآلة (LDA) للبحث عن 5 مواضيع...
✅ اكتمل بناء النموذج!

🎉 النتائج: أهم 10 كلمات مفتاحية لكل موضوع من المواضيع الـ 5

🎨 **الموضوع رقم #1:**
ان | السعوديه | او | بن | العمل | المملكه | عام | ترمب | المقال | مدينه

🎨 **الموضوع رقم #2:**
جده | عبدالله | البيانات | المنشات | وفن | ثقافه | الهيئه | المقال | ذكري | ازياء

🎨 **الموضوع رقم #3:**
السعوديين | الاتحاد | الاغلاق | الحكومي | نقطه | بنسبه | اللقاء | الخليج | الاسهم | السعوديه

🎨 **الموضوع رقم #4:**
الرقميه | وزير | الاماكن | الثقافه | سعود | الحارس | النصر | والمحافظه | وفن | ثقافه

🎨 **الموضوع رقم #5:**
الفنانه | امام | وفن | موسم | مطار | ثقافه | المطار | المكسيك | يوم | الفني

انتهت المهمة. هذه هي المجموعات الرئيسية للمواضيع في مقالات عكاظ التي جمعتها.


In [10]:
# --- الخطوة 1: تثبيت الترسانة ---
print("🔧 جاري تثبيت المكتبات (Transformers, Datasets, Hugging Face Hub)...")
!pip install transformers datasets huggingface_hub
print("✅ اكتمل تثبيت الترسانة.")

🔧 جاري تثبيت المكتبات (Transformers, Datasets, Hugging Face Hub)...
✅ اكتمل تثبيت الترسانة.


In [11]:
# --- الخطوة 2: تسجيل الدخول ---
from huggingface_hub import notebook_login

print("🔑 الرجاء إدخال رمز (Token) Hugging Face الخاص بك (مع صلاحية 'write').")
notebook_login()

🔑 الرجاء إدخال رمز (Token) Hugging Face الخاص بك (مع صلاحية 'write').


In [13]:
# ==============================================================================
#  الكود (الخطوة 3.1 - إصلاح مشكلة wandb)
# ==============================================================================

import pandas as pd
import os
from datasets import load_dataset, Dataset
from transformers import AutoTokenizer, DataCollatorForLanguageModeling
from transformers import AutoModelForMaskedLM
from transformers import TrainingArguments, Trainer

# --- 3.1: تحديد الإعدادات ---
MODEL_NAME = "aubmindlab/bert-base-arabertv2"
NEW_MODEL_NAME = "ara-bert-okaz-style"
CLEANED_FILE = "/content/drive/MyDrive/Scraped_Data/okaz_articles_cleaned.csv"

print(f"🔧 سنقوم بتدريب المودل {MODEL_NAME} لإنشاء مودل جديد باسم {NEW_MODEL_NAME}")

# --- 3.2: تحميل البيانات ---
print(f"🔄 1. جاري تحميل ملف CSV النظيف من: {CLEANED_FILE}")
try:
    df = pd.read_csv(CLEANED_FILE)
    df['cleaned_content'] = df['cleaned_content'].fillna('')
    dataset = Dataset.from_pandas(df)
    dataset = dataset.rename_column("cleaned_content", "text")
    cols_to_remove = [col for col in dataset.column_names if col not in ['text', 'url']]
    dataset = dataset.remove_columns(cols_to_remove)
    print(f"✅ تم تحميل {len(dataset)} مقالاً وجاهز للمعالجة.")
except FileNotFoundError:
    print(f"❌ خطأ: لم يتم العثور على الملف {CLEANED_FILE}.")
    print("✋ الرجاء التأكد من تشغيل كود (المرحلة 1: التنظيف) أولاً.")
    raise Exception("توقف التنفيذ: الملف النظيف غير موجود")
except Exception as e:
    print(f"❌ خطأ غير متوقع أثناء تحميل البيانات: {e}")
    raise

# --- 3.3: تحميل المُقطّع (Tokenizer) ---
print("\n🔄 2. جاري تحميل (المُقطّع) الخاص بـ AraBERT...")
tokenizer = AutoTokenizer.from_pretrained(MODEL_NAME)
print("✅ تم تحميل المُقطّع.")

# --- 3.4: تقطيع (Tokenize) جميع المقالات ---
def tokenize_function(examples):
    return tokenizer(examples["text"], truncation=True, max_length=512, padding=False)

print(f"\n🔄 3. جاري تحويل الـ {len(dataset)} مقالاً إلى أرقام (Tokenizing)...")
tokenized_dataset = dataset.map(tokenize_function, batched=True, remove_columns=["text", "url"])
print("✅ اكتمل التحويل!")

# --- 3.5: إعداد مهمة "إملأ الفراغ" (MLM) ---
print("\n🔄 4. جاري إعداد مهمة (إخفاء الكلمات) - MLM...")
data_collator = DataCollatorForLanguageModeling(
    tokenizer=tokenizer,
    mlm=True,
    mlm_probability=0.15
)
print("✅ جاهز للتدريب. البيانات أصبحت مُقنّعة وجاهزة للتخمين.")

# --- 3.6: تحميل المودل الأساسي ---
print(f"\n🔄 5. جاري تحميل المودل الأساسي ({MODEL_NAME})...")
model = AutoModelForMaskedLM.from_pretrained(MODEL_NAME)
print("✅ تم تحميل المودل.")

# --- 3.7: إعداد إعدادات التدريب ---
print("\n🔄 6. جاري إعداد إعدادات التدريب...")
training_args = TrainingArguments(
    output_dir=NEW_MODEL_NAME,
    overwrite_output_dir=True,
    num_train_epochs=10,
    per_device_train_batch_size=8,
    save_strategy="epoch",
    push_to_hub=True,
    logging_steps=10,

    # [ --- هذا هو السطر الجديد الذي يحل المشكلة --- ]
    report_to="none",
    # [ -------------------------------------------- ]
)

# --- 3.8: تجميع "المدرب" (Trainer) ---
print("🔄 7. جاري تجميع (المدرب)...")
trainer = Trainer(
    model=model,
    args=training_args,
    data_collator=data_collator,
    train_dataset=tokenized_dataset,
)

# --- 3.9: بدء التدريب! ---
print("\n" + "="*50)
print("🚀🚀🚀 بدء عملية التدريب (Fine-Tuning)! 🚀🚀🚀")
print("...سيقوم المودل الآن بقراءة مقالات عكاظ ومحاولة تخمين الكلمات المخفية...")
trainer.train()
print("🎉🎉🎉 اكتمل التدريب بنجاح! 🎉🎉🎉")
print("="*50)

# --- 3.10: الرفع النهائي (للتأكيد) ---
print(f"\n🔄 8. جاري رفع المودل النهائي وملف (المُقطّع) إلى '{NEW_MODEL_NAME}' في حسابك...")
try:
    trainer.push_to_hub(commit_message="التدريب الأولي على 143 مقالاً من عكاظ")
    print(f"✅ تم الرفع بنجاح! مودلك أصبح متوفراً على hf.co/{training_args.hub_token.whoami}/{NEW_MODEL_NAME}")
except Exception as e:
    print(f"❌ حدث خطأ أثناء محاولة الرفع. لا تقلق، المودل تم تدريبه وحفظه محلياً في مجلد '{NEW_MODEL_NAME}'.")
    print(f"الخطأ: {e}")

🔧 سنقوم بتدريب المودل aubmindlab/bert-base-arabertv2 لإنشاء مودل جديد باسم ara-bert-okaz-style
🔄 1. جاري تحميل ملف CSV النظيف من: /content/drive/MyDrive/Scraped_Data/okaz_articles_cleaned.csv
✅ تم تحميل 143 مقالاً وجاهز للمعالجة.

🔄 2. جاري تحميل (المُقطّع) الخاص بـ AraBERT...
✅ تم تحميل المُقطّع.

🔄 3. جاري تحويل الـ 143 مقالاً إلى أرقام (Tokenizing)...


Map:   0%|          | 0/143 [00:00<?, ? examples/s]

✅ اكتمل التحويل!

🔄 4. جاري إعداد مهمة (إخفاء الكلمات) - MLM...
✅ جاهز للتدريب. البيانات أصبحت مُقنّعة وجاهزة للتخمين.

🔄 5. جاري تحميل المودل الأساسي (aubmindlab/bert-base-arabertv2)...


Some weights of the model checkpoint at aubmindlab/bert-base-arabertv2 were not used when initializing BertForMaskedLM: ['bert.pooler.dense.bias', 'bert.pooler.dense.weight', 'cls.seq_relationship.bias', 'cls.seq_relationship.weight']
- This IS expected if you are initializing BertForMaskedLM from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing BertForMaskedLM from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).


✅ تم تحميل المودل.

🔄 6. جاري إعداد إعدادات التدريب...
🔄 7. جاري تجميع (المدرب)...

🚀🚀🚀 بدء عملية التدريب (Fine-Tuning)! 🚀🚀🚀
...سيقوم المودل الآن بقراءة مقالات عكاظ ومحاولة تخمين الكلمات المخفية...


...

New Data Upload               : |          |  0.00B /  0.00B            

  ...z-style/training_args.bin: 100%|##########| 5.84kB / 5.84kB            

  ...84319.da3d9d6af63c.1620.0: 100%|##########| 4.98kB / 4.98kB            

  ...z-style/model.safetensors:   6%|6         | 33.5MB /  541MB            

❌ حدث خطأ أثناء محاولة الرفع. لا تقلق، المودل تم تدريبه وحفظه محلياً في مجلد 'ara-bert-okaz-style'.
الخطأ: 'NoneType' object has no attribute 'whoami'


In [15]:
# ==============================================================================
#  الخطوة 4.1: الرفع اليدوي (تصحيح خطأ 404)
# ==============================================================================
from huggingface_hub import HfApi, create_repo
import os

# --- 4.1: الإعدادات ---
MODEL_BASENAME = "ara-bert-okaz-style" # الاسم الأساسي
LOCAL_MODEL_DIR = "./" + MODEL_BASENAME

print(f"🔄 جاري محاولة رفع المودل من المجلد المحلي: {LOCAL_MODEL_DIR}")

try:
    api = HfApi()

    # 1. جلب اسم المستخدم (لإصلاح خطأ 404)
    user_info = api.whoami()
    username = user_info['name']
    print(f"✅ تم التعرف عليك باسم المستخدم: {username}")

    # 2. إنشاء اسم المستودع الكامل (Full Repo ID)
    FULL_REPO_ID = f"{username}/{MODEL_BASENAME}"
    print(f"🔧 سيتم الرفع إلى المستودع: {FULL_REPO_ID}")

    # --- 4.2: إنشاء المستودع (Repo) ---
    print(f"🔄 جاري إنشاء/تأكيد المستودع: {FULL_REPO_ID}...")
    # (نستخدم الـ ID الكامل للتأكيد)
    repo_url = create_repo(repo_id=FULL_REPO_ID, exist_ok=True, private=False) # private=False لجعله عاماً
    print(f"✅ المستودع جاهز: {repo_url}")

    # --- 4.3: رفع الملفات ---
    print(f"🚀 جاري رفع جميع الملفات من {LOCAL_MODEL_DIR} إلى المستودع...")

    # [هذا هو الإصلاح] استخدام الـ ID الكامل (FULL_REPO_ID)
    api.upload_folder(
        folder_path=LOCAL_MODEL_DIR,
        repo_id=FULL_REPO_ID,
        repo_type="model",
        commit_message="رفع المودل المدرب (إصدار 1) - 143 مقالاً من عكاظ"
    )

    print("\n" + "="*50)
    print(f"🎉🎉🎉 تم رفع المودل بنجاح! 🎉🎉🎉")
    print(f"يمكنك الآن رؤية مودلك الخاص على الرابط:")
    print(f"https://huggingface.co/{FULL_REPO_ID}") # طباعة الرابط الكامل
    print("="*50)

except Exception as e:
    print(f"❌ حدث خطأ كبير أثناء الرفع اليدوي. الخطأ: {e}")
    print("لا تقلق، المودل لا يزال محفوظاً محلياً. تحقق من اتصالك بالإنترنت ومن الرمز (Token).")

🔄 جاري محاولة رفع المودل من المجلد المحلي: ./ara-bert-okaz-style
✅ تم التعرف عليك باسم المستخدم: alomari7
🔧 سيتم الرفع إلى المستودع: alomari7/ara-bert-okaz-style
🔄 جاري إنشاء/تأكيد المستودع: alomari7/ara-bert-okaz-style...
✅ المستودع جاهز: https://huggingface.co/alomari7/ara-bert-okaz-style
🚀 جاري رفع جميع الملفات من ./ara-bert-okaz-style إلى المستودع...


Processing Files (0 / 0)      : |          |  0.00B /  0.00B            

New Data Upload               : |          |  0.00B /  0.00B            

  ...z-style/training_args.bin: 100%|##########| 5.84kB / 5.84kB            

  ...oint-18/training_args.bin: 100%|##########| 5.84kB / 5.84kB            

...

  ...oint-36/training_args.bin: 100%|##########| 5.84kB / 5.84kB            

  ...oint-54/model.safetensors:   2%|1         | 8.38MB /  541MB            

  ...eckpoint-180/scheduler.pt: 100%|##########| 1.47kB / 1.47kB            

  ...eckpoint-180/optimizer.pt:   0%|          |  527kB / 1.08GB            


🎉🎉🎉 تم رفع المودل بنجاح! 🎉🎉🎉
يمكنك الآن رؤية مودلك الخاص على الرابط:
https://huggingface.co/alomari7/ara-bert-okaz-style


In [16]:
# حذف المجلد المحلي للمودل (16.8 جيجا)
!rm -rf ./ara-bert-okaz-style
print("✅ تم حذف المجلد المحلي للمودل وتوفير 16.8 جيجا من مساحة Colab.")

✅ تم حذف المجلد المحلي للمودل وتوفير 16.8 جيجا من مساحة Colab.


In [17]:
# ==============================================================================
#  الخطوة 5: توثيق المشروع ورفعه إلى GitHub
# ==============================================================================

# --- 5.1: إنشاء ملف التوثيق (README.md) ---
print("✍️ جاري كتابة ملف التوثيق (README.md)...")

# (لقد كتبت لك ملف توثيق احترافي جاهز)
# هو يربط تلقائياً بمودلك على Hugging Face الذي أنشأته
README_CONTENT = """
# مشروع سحب وتحليل مقالات عكاظ (Okaz NLP Project)

هذا المشروع هو عبارة عن خط أنابيب (Pipeline) كامل لمعالجة اللغات الطبيعية (NLP)، يبدأ من سحب البيانات الحية وينتهي بإنشاء مودل لغوي مُصقل (Fine-Tuned).

## 🚀 المودل المدرب (Fine-Tuned Model)

النتيجة النهائية لهذا المشروع هو مودل لغوي عربي مُعدل على أسلوب مقالات عكاظ.
**المودل متاح على Hugging Face هنا:**
[https://huggingface.co/alomari7/ara-bert-okaz-style](https://huggingface.co/alomari7/ara-bert-okaz-style)

---

## 🔧 مكونات المشروع

هذا المستودع يحتوي على الكود الكامل للمشروع، مقسماً إلى 3 مراحل:

### 1. السحب (Scraping)
- **الكود:** `scraper_v13.py` (أو `scapping2.ipynb`)
- **الهدف:** سحب المقالات الحية من موقع "عكاظ".
- **الاستراتيجية (إصدار 13):**
    1.  يستخدم `undetected-chromedriver` لتجاوز حماية الموقع.
    2.  يقوم بـ "الزحف العميق" (Deep Crawl) لـ 6 أقسام رئيسية (محليات، سياسة، اقتصاد، رياضة، ثقافة، منوعات).
    3.  يجمع كل روابط المقالات من الصفحات الأولى لهذه الأقسام.
    4.  يقارن الروابط الجديدة بالملف المحفوظ (`okaz_articles_full.csv`) ويسحب المقالات الجديدة فقط.
    5.  يحفظ البيانات في `okaz_articles_full.csv`.

### 2. التنظيف والمعالجة (Cleaning & Analysis)
- **الكود:** `analysis.py`
- **الهدف:** تحويل البيانات الخام إلى بيانات نظيفة جاهزة للتحليل وتعلم الآلة.
- **الخطوات:**
    1.  **التنظيف:** تحميل `okaz_articles_full.csv`، إزالة الضجيج (مثل "اقرأ أيضاً")، وحفظه في `okaz_articles_cleaned.csv`.
    2.  **تحليل التكرار:** قراءة الملف النظيف، إزالة الكلمات المستبعدة (Stop Words)، وعدّ الكلمات الأكثر تكراراً لحفظها في `okaz_word_frequency.csv`.

### 3. التدريب (Fine-Tuning)
- **الكود:** `fine_tuning.ipynb`
- **الهدف:** صقل (Fine-Tune) مودل لغوي على بياناتنا.
- **الخطوات:**
    1.  **المودل الأساسي:** `aubmindlab/bert-base-arabertv2` (AraBERT).
    2.  **المهمة:** Masked Language Modeling (MLM) - جعل المودل يتنبأ بالكلمات المخفية في مقالات عكاظ.
    3.  **البيانات:** 143 مقالاً نظيفاً.
    4.  **النتيجة:** مودل `ara-bert-okaz-style` الجديد.

---

## ⚙️ كيفية تشغيل المشروع
1.  تأكد من وجود جميع المكتبات (انظر ملف `requirements.txt` أو الكود).
2.  قم بتشغيل كود السحب (`scraper_v13.py`) لجمع البيانات.
3.  قم بتشغيل كود التحليل (`analysis.py`) لتنظيفها.
4.  (اختياري) قم بتشغيل كود التدريب لإنشاء المودل الخاص بك.
"""

with open("README.md", "w", encoding="utf-8") as f:
    f.write(README_CONTENT)
print("✅ تم إنشاء README.md بنجاح.")

# --- 5.2: إنشاء ملف (gitignore) ---
print("✍️ جاري كتابة ملف .gitignore...")
GITIGNORE_CONTENT = """
# تجاهل الملفات المحلية والبيانات الحساسة
.ipynb_checkpoints/
__pycache__/
*.csv
/content/drive/
ara-bert-okaz-style/
*.zip
*.deb
chromedriver
"""
with open(".gitignore", "w", encoding="utf-8") as f:
    f.write(GITIGNORE_CONTENT)
print("✅ تم إنشاء .gitignore بنجاح.")

# --- 5.3: تسجيل الدخول إلى GitHub ---
# نحتاج لتثبيت هذه المكتبة لنتعامل مع GitHub
!pip install huggingface_hub
from huggingface_hub import HfApi, HfFolder, create_repo, notebook_login

print("\n🔑 الرجاء تسجيل الدخول إلى GitHub.")
print("ملاحظة: أنت لا تحتاج إلى 'رمز' (Token) جديد، يمكنك استخدام نفس الرمز الذي استخدمته لـ Hugging Face.")
notebook_login()

# --- 5.4: إنشاء ورفع المشروع إلى GitHub ---
print("\n🚀 جاري إنشاء ورفع المشروع إلى GitHub...")

try:
    api = HfApi()

    # جلب اسم المستخدم (لإنشاء المستودع بالاسم الصحيح)
    user_info = api.whoami()
    username = user_info['name']

    GITHUB_REPO_ID = f"{username}/Okaz-NLP-Project"

    print(f"🔧 سيتم إنشاء المستودع باسم: {GITHUB_REPO_ID}")

    # 1. إنشاء المستودع على GitHub
    create_repo(repo_id=GITHUB_REPO_ID, repo_type="space", space_sdk="static", exist_ok=True)
    print(f"✅ تم إنشاء مستودع GitHub (أو تأكيده): https://huggingface.co/spaces/{GITHUB_REPO_ID}")
    print("ملاحظة: يتم استضافة مشاريع GitHub على 'Spaces' في Hugging Face.")

    # 2. رفع ملفات التوثيق
    # (سنرفع فقط ملفات التوثيق والكود، وليس البيانات أو المودل)
    api.upload_file(
        path_or_fileobj="README.md",
        path_in_repo="README.md",
        repo_id=GITHUB_REPO_ID,
        repo_type="space"
    )
    api.upload_file(
        path_or_fileobj=".gitignore",
        path_in_repo=".gitignore",
        repo_id=GITHUB_REPO_ID,
        repo_type="space"
    )

    print("\n" + "="*50)
    print(f"🎉🎉🎉 تم رفع ملفات التوثيق بنجاح! 🎉🎉🎉")
    print("المشروع أصبح موثقاً وجاهزاً للمشاركة.")
    print(f"🔗 رابط المشروع على (GitHub/Hugging Face Spaces): https://huggingface.co/spaces/{GITHUB_REPO_ID}")
    print("="*50)

    print("\n💡 **هام جداً:**")
    print("لإضافة ملفات الكود (ملفات .ipynb)، اذهب إلى الرابط أعلاه، واختر 'Files and versions'،")
    print("ثم اختر 'Add file' -> 'Upload file' وقم برفع ملفات Colab الخاصة بك يدوياً.")

except Exception as e:
    print(f"❌ حدث خطأ أثناء الرفع إلى GitHub: {e}")

✍️ جاري كتابة ملف التوثيق (README.md)...
✅ تم إنشاء README.md بنجاح.
✍️ جاري كتابة ملف .gitignore...
✅ تم إنشاء .gitignore بنجاح.

🔑 الرجاء تسجيل الدخول إلى GitHub.
ملاحظة: أنت لا تحتاج إلى 'رمز' (Token) جديد، يمكنك استخدام نفس الرمز الذي استخدمته لـ Hugging Face.



🚀 جاري إنشاء ورفع المشروع إلى GitHub...
🔧 سيتم إنشاء المستودع باسم: alomari7/Okaz-NLP-Project
✅ تم إنشاء مستودع GitHub (أو تأكيده): https://huggingface.co/spaces/alomari7/Okaz-NLP-Project
ملاحظة: يتم استضافة مشاريع GitHub على 'Spaces' في Hugging Face.


/usr/local/lib/python3.12/dist-packages/huggingface_hub/hf_api.py:9662: UserWarning: Warnings while validating metadata in README.md:
- empty or missing yaml metadata in repo card
  warnings.warn(f"Warnings while validating metadata in README.md:\n{message}")



🎉🎉🎉 تم رفع ملفات التوثيق بنجاح! 🎉🎉🎉
المشروع أصبح موثقاً وجاهزاً للمشاركة.
🔗 رابط المشروع على (GitHub/Hugging Face Spaces): https://huggingface.co/spaces/alomari7/Okaz-NLP-Project

💡 **هام جداً:**
لإضافة ملفات الكود (ملفات .ipynb)، اذهب إلى الرابط أعلاه، واختر 'Files and versions'،
ثم اختر 'Add file' -> 'Upload file' وقم برفع ملفات Colab الخاصة بك يدوياً.


In [18]:
# ==============================================================================
#  الخطوة 6 (النهائية): رفع الكود المُوثق بالكامل إلى GitHub/HF Space
# ==============================================================================
from huggingface_hub import HfApi, HfFolder, create_repo, notebook_login
import os

# --- 6.1: الإعدادات ---
# (يجب أن يتطابق تماماً مع ما أنشأناه)
MODEL_BASENAME = "ara-bert-okaz-style"
GITHUB_BASENAME = "Okaz-NLP-Project"
LOCAL_MODEL_DIR = "./" + MODEL_BASENAME

# اسم ملف Colab Notebook الذي نعمل عليه الآن
# (سيقوم الكود بحفظه ورفعه)
PROJECT_NOTEBOOK_NAME = "Okaz_Project_Main.ipynb"


# --- 6.2: إنشاء ملف التوثيق المُحسّن (README.md) ---
print("✍️ جاري كتابة ملف التوثيق المُحسّن (README.md) مع إعدادات YAML...")

# [تم التعديل] أضفنا رأس الإعدادات في الأعلى لإرضاء Hugging Face Spaces
README_CONTENT = """
---
title: مشروع سحب وتحليل مقالات عكاظ
emoji: 📰
colorFrom: blue
colorTo: green
sdk: static
---

# مشروع سحب وتحليل مقالات عكاظ (Okaz NLP Project)

هذا المشروع هو عبارة عن خط أنابيب (Pipeline) كامل لمعالجة اللغات الطبيعية (NLP)، يبدأ من سحب البيانات الحية وينتهي بإنشاء مودل لغوي مُصقل (Fine-Tuned).

## 🚀 المودل المدرب (Fine-Tuned Model)

النتيجة النهائية لهذا المشروع هو مودل لغوي عربي مُعدل على أسلوب مقالات عكاظ.
**المودل متاح على Hugging Face هنا:**
[https://huggingface.co/alomari7/ara-bert-okaz-style](https://huggingface.co/alomari7/ara-bert-okaz-style)

---

## 🔧 مكونات المشروع

هذا المستودع يحتوي على الكود الكامل للمشروع، مقسماً إلى 3 مراحل:

### 1. السحب (Scraping)
- **الكود:** `Okaz_Project_Main.ipynb` (انظر هذا الملف)
- **الهدف:** سحب المقالات الحية من موقع "عكاظ".
- **الاستراتيجية (إصدار 13):**
    1.  يستخدم `undetected-chromedriver` لتجاوز حماية الموقع.
    2.  يقوم بـ "الزحف العميق" (Deep Crawl) لـ 6 أقسام رئيسية (محليات، سياسة، اقتصاد، رياضة، ثقافة، منوعات).
    3.  يجمع كل روابط المقالات من الصفحات الأولى لهذه الأقسام.
    4.  يقارن الروابط الجديدة بالملف المحفوظ (`okaz_articles_full.csv`) ويسحب المقالات الجديدة فقط.
    5.  يحفظ البيانات في `okaz_articles_full.csv`.

### 2. التنظيف والمعالجة (Cleaning & Analysis)
- **الكود:** `Okaz_Project_Main.ipynb` (انظر هذا الملف)
- **الهدف:** تحويل البيانات الخام إلى بيانات نظيفة جاهزة للتحليل وتعلم الآلة.
- **الخطوات:**
    1.  **التنظيف:** تحميل `okaz_articles_full.csv`، إزالة الضجيج (مثل "اقرأ أيضاً")، وحفظه في `okaz_articles_cleaned.csv`.
    2.  **تحليل التكرار:** قراءة الملف النظيف، إزالة الكلمات المستبعدة (Stop Words)، وعدّ الكلمات الأكثر تكراراً لحفظها في `okaz_word_frequency.csv`.
    3.  **نمذجة المواضيع:** استخدام (LDA) على الملف النظيف لاكتشاف 5 مواضيع رئيسية مخبأة في البيانات.

### 3. التدريب (Fine-Tuning)
- **الكود:** `Okaz_Project_Main.ipynb` (انظر هذا الملف)
- **الهدف:** صقل (Fine-Tune) مودل لغوي على بياناتنا.
- **الخطوات:**
    1.  **المودل الأساسي:** `aubmindlab/bert-base-arabertv2` (AraBERT).
    2.  **المهمة:** Masked Language Modeling (MLM).
    3.  **البيانات:** 143 مقالاً نظيفاً.
    4.  **النتيجة:** مودل `alomari7/ara-bert-okaz-style` الجديد.

---

## ⚙️ كيفية تشغيل المشروع
1.  افتح `Okaz_Project_Main.ipynb` في Google Colab.
2.  تأكد من وجود المكتبات (الكود يتضمن أوامر التثبيت).
3.  قم بتشغيل الخلايا بالتسلسل.
"""

with open("README.md", "w", encoding="utf-8") as f:
    f.write(README_CONTENT)
print("✅ تم إنشاء README.md المُحسّن بنجاح.")

# --- 6.3: حفظ ملف Colab Notebook الحالي ---
print(f"🔄 جاري حفظ ملف Colab Notebook الحالي باسم: {PROJECT_NOTEBOOK_NAME} ...")
# هذا الكود "السحري" يتطلب تفاعلاً يدوياً منك لحفظ الملف
# الرجاء القيام بذلك يدوياً:
# 1. من قائمة "ملف" (File) في Colab
# 2. اختر "حفظ نسخة في Drive" (Save a copy in Drive)
# 3. بعد أن يفتح الملف الجديد، قم بـ "إعادة تسميته" (Rename) إلى Okaz_Project_Main.ipynb
# 4. تأكد أنه محفوظ في جذر Google Drive الخاص بك أو في مجلد يسهل الوصول إليه.

# *** هذه خطوة يدوية، لا يمكننا أتمتتها بالكامل ***
print(f"‼️ **إجراء مطلوب:** قم بحفظ هذا الملف (Notebook) في Google Drive باسم `{PROJECT_NOTEBOOK_NAME}`.")
print("...سننتظر 10 ثوانٍ للتأكد من أنك قرأت الرسالة، ثم سنحاول الرفع من المسار الافتراضي...")
time.sleep(10)


# --- 6.4: رفع كل شيء إلى GitHub/HF Space ---
print("\n🚀 جاري رفع المشروع بالكامل إلى Hugging Face Spaces...")

try:
    api = HfApi()

    # جلب اسم المستخدم (لإنشاء المستودع بالاسم الصحيح)
    user_info = api.whoami()
    username = user_info['name']
    GITHUB_REPO_ID = f"{username}/{GITHUB_BASENAME}"

    print(f"🔧 المستودع المستهدف: {GITHUB_REPO_ID}")

    # 1. رفع ملف README.md (الكتابة فوق القديم)
    api.upload_file(
        path_or_fileobj="README.md",
        path_in_repo="README.md",
        repo_id=GITHUB_REPO_ID,
        repo_type="space"
    )
    print("✅ تم رفع README.md المُحسّن.")

    # 2. رفع ملف .gitignore (الكتابة فوق القديم)
    api.upload_file(
        path_or_fileobj=".gitignore",
        path_in_repo=".gitignore",
        repo_id=GITHUB_REPO_ID,
        repo_type="space"
    )
    print("✅ تم رفع .gitignore.")

    # 3. [الأهم] رفع ملف الكود (ipynb)
    # نفترض أنك حفظته في جذر Drive (أو قم بتعديل المسار)
    # ملاحظة: إذا كنت تعمل في Colab، قد تحتاج لرفعه يدوياً كما ذكر السجل السابق
    # لكننا سنحاول العثور عليه في Drive

    # سنبحث عنه في المسار الافتراضي الذي يحفظ فيه Colab
    notebook_path_in_drive = f"/content/drive/MyDrive/Colab Notebooks/{PROJECT_NOTEBOOK_NAME}"

    if not os.path.exists(notebook_path_in_drive):
        # إذا لم نجده، سنبحث في الجذر
        notebook_path_in_drive = f"/content/drive/MyDrive/{PROJECT_NOTEBOOK_NAME}"

    if os.path.exists(notebook_path_in_drive):
        print(f"✅ تم العثور على ملف الكود في: {notebook_path_in_drive}")
        api.upload_file(
            path_or_fileobj=notebook_path_in_drive,
            path_in_repo=PROJECT_NOTEBOOK_NAME, # الاسم الذي سيظهر في المستودع
            repo_id=GITHUB_REPO_ID,
            repo_type="space"
        )
        print(f"✅ تم رفع ملف الكود {PROJECT_NOTEBOOK_NAME} بنجاح!")
    else:
        print(f"⚠️ **تحذير:** لم أتمكن من العثور على `{PROJECT_NOTEBOOK_NAME}` في Google Drive.")
        print("الرجاء رفعه يدوياً إلى المستودع.")

    print("\n" + "="*50)
    print(f"🎉🎉🎉 اكتمل المشروع! 🎉🎉🎉")
    print("أصبح لديك الآن مستودع كود، ومودل لغوي يعمل!")
    print(f"🔗 رابط المودل: https://huggingface.co/{username}/{MODEL_BASENAME}")
    print(f"🔗 رابط المشروع (GitHub/Space): https://huggingface.co/spaces/{GITHUB_REPO_ID}")
    print("="*50)

except Exception as e:
    print(f"❌ حدث خطأ أثناء الرفع النهائي: {e}")

✍️ جاري كتابة ملف التوثيق المُحسّن (README.md) مع إعدادات YAML...
✅ تم إنشاء README.md المُحسّن بنجاح.
🔄 جاري حفظ ملف Colab Notebook الحالي باسم: Okaz_Project_Main.ipynb ...
‼️ **إجراء مطلوب:** قم بحفظ هذا الملف (Notebook) في Google Drive باسم `Okaz_Project_Main.ipynb`.
...سننتظر 10 ثوانٍ للتأكد من أنك قرأت الرسالة، ثم سنحاول الرفع من المسار الافتراضي...

🚀 جاري رفع المشروع بالكامل إلى Hugging Face Spaces...
🔧 المستودع المستهدف: alomari7/Okaz-NLP-Project
✅ تم رفع README.md المُحسّن.


No files have been modified since last commit. Skipping to prevent empty commit.


✅ تم رفع .gitignore.
⚠️ **تحذير:** لم أتمكن من العثور على `Okaz_Project_Main.ipynb` في Google Drive.
الرجاء رفعه يدوياً إلى المستودع.

🎉🎉🎉 اكتمل المشروع! 🎉🎉🎉
أصبح لديك الآن مستودع كود، ومودل لغوي يعمل!
🔗 رابط المودل: https://huggingface.co/alomari7/ara-bert-okaz-style
🔗 رابط المشروع (GitHub/Space): https://huggingface.co/spaces/alomari7/Okaz-NLP-Project
